In [20]:
import pymongo
from pymongo import MongoClient
import pandas as pd
import numpy as np
from bs4 import BeautifulSoup
import copy

In [2]:
client = MongoClient()

In [3]:
client.list_database_names()

['PairExDb',
 'admin',
 'boxscores',
 'config',
 'local',
 'nyt_dump',
 'spreads',
 'spreadscombined']

In [4]:
spreadscombined = client['spreadscombined']

In [6]:
data = pd.DataFrame(list(spreadscombined.unified.find()))

In [7]:
def create_dct_content_spread(df):
    biglist = {}
    for i in range(len(df.content)):
        if df.team[i] not in biglist.keys():
            biglist[df.team[i]] = {}
        if df.year[i] not in biglist[df.team[i]].keys():
            biglist[df.team[i]][df.year[i]] = {}
        soup = BeautifulSoup(df.content[i], 'html.parser')
        for count,items in enumerate(soup.select('tbody tr'),1):
            biglist[df.team[i]][df.year[i]][count] = []
            temp = []
            for item in items.select('td'):
                temp.append(item.get_text())
            biglist[df.team[i]][df.year[i]][count] += temp
    return biglist

In [67]:
create_dct_content_spread(data)

{'ATL': {'2014': {1: ['Oct 30, 2013',
    '  @  Dallas',
    'REG',
    'L',
    ' 118-109',
    'L',
    ' +6',
    'O',
    '196'],
   2: ['Nov 1, 2013',
    '  vs  Toronto',
    'REG',
    'W',
    ' 102-95',
    'W',
    ' -3.5',
    'O',
    '196'],
   3: ['Nov 3, 2013',
    '  @  LA Lakers',
    'REG',
    'L',
    ' 105-103',
    'L',
    ' -1',
    'O',
    '205'],
   4: ['Nov 5, 2013',
    '  @  Sacramento',
    'REG',
    'W',
    ' 105-100',
    'W',
    ' +2',
    'O',
    '200'],
   5: ['Nov 7, 2013',
    '  @  Denver',
    'REG',
    'L',
    ' 109-107',
    'W',
    ' +4.5',
    'O',
    '204'],
   6: ['Nov 9, 2013',
    '  vs  Orlando',
    'REG',
    'W',
    ' 104-94',
    'W',
    ' -6.5',
    'U',
    '199'],
   7: ['Nov 11, 2013',
    '  @  Charlotte',
    'REG',
    'W',
    ' 103-94',
    'W',
    ' -2',
    'O',
    '196'],
   8: ['Nov 13, 2013',
    '  vs  New York',
    'REG',
    'L',
    ' 95-91',
    'L',
    ' -4.5',
    'U',
    '201.5'],
   9: ['Nov 15, 

In [68]:
test = _

In [69]:
spread_data = [[team,year,game,test[team][year][game][0],test[team][year][game][1],test[team][year][game][2],test[team][year][game][3],test[team][year][game][4],test[team][year][game][5],test[team][year][game][6],test[team][year][game][7],test[team][year][game][8]] for team in test.keys() for year in test[team].keys() for game in test[team][year].keys()]

In [70]:
spread_df = pd.DataFrame(data=spread_data)

In [71]:
spread_df.columns =['team','year','g','date','opp','gametype','result','score','ats','spread','ou','total']

In [72]:
df = copy.deepcopy(spread_df[spread_df.gametype == 'REG'])

In [73]:
ats = df.ats.apply(lambda x: 0.0 if x=='L' else 1.0).values

In [74]:
df.index = range(1,12301)

In [75]:
df.index = list(range(1,12301))

In [76]:
df.ats = ats

In [77]:
spread = df.spread.apply(lambda x: 0.0 if 'Ev' in x else float(x) ).values

In [78]:
df.spread = spread

In [79]:
df.drop(columns=['gametype'],inplace=True)

In [80]:
home = df.opp.apply(lambda x: 0 if '@' in x else 1).values

In [81]:
df['home'] = home

In [82]:
result = df.result.apply(lambda x: 0 if x=='L' else 1).values
df.result = result
score = df.score.apply(lambda x: x.split('-')).values


In [85]:
df.score = score

In [86]:
def scorer(x):
    lst = []
    for num in x:
        lst.append(float(num))
    return lst

In [87]:
score = df.score.apply(scorer).values

In [88]:
df.score = score

In [94]:
lst = []
for i in range(1,len(df)+1):
    if df.result[i] == 1:
        lst.append(df.score[i][0] - df.score[i][1])
    else:
        lst.append(df.score[i][1] - df.score[i][0])

In [97]:
df['score_diff'] = lst

In [99]:
df['spread_diff'] = df.score_diff + df.spread

In [101]:
df_test = copy.deepcopy(df[['spread','home','score_diff','spread_diff']])

In [106]:
X = df_test
y = df.ats.values

In [107]:
y

array([0., 1., 0., ..., 0., 0., 1.])

In [110]:
from sklearn.linear_model import LogisticRegression
from sklearn.cross_validation import train_test_split

In [111]:
lr = LogisticRegression()

In [124]:
X_train, X_test, y_train, y_test = train_test_split(X,y, test_size=0.1)

In [128]:
lr.fit(X_test,y_test)

LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_state=None, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False)

In [131]:
df

team  year   g          date                  opp  result  \
1      ATL  2014   1  Oct 30, 2013            @  Dallas       0   
2      ATL  2014   2   Nov 1, 2013          vs  Toronto       1   
3      ATL  2014   3   Nov 3, 2013         @  LA Lakers       0   
4      ATL  2014   4   Nov 5, 2013        @  Sacramento       1   
5      ATL  2014   5   Nov 7, 2013            @  Denver       0   
6      ATL  2014   6   Nov 9, 2013          vs  Orlando       1   
7      ATL  2014   7  Nov 11, 2013         @  Charlotte       1   
8      ATL  2014   8  Nov 13, 2013         vs  New York       0   
9      ATL  2014   9  Nov 15, 2013     vs  Philadelphia       1   
10     ATL  2014  10  Nov 16, 2013          @  New York       1   
11     ATL  2014  11  Nov 19, 2013             @  Miami       0   
12     ATL  2014  12  Nov 20, 2013          vs  Detroit       1   
13     ATL  2014  13  Nov 22, 2013           @  Detroit       1   
14     ATL  2014  14  Nov 23, 2013           vs  Boston       0   
15     ATL  2014  15  Nov 26, 2013          vs  Orlando       0   
16     ATL  2014  16  Nov 27, 2013           @  Houston       0   
17     ATL  2014  17  Nov 29, 2013           vs  Dallas       1   
18     ATL  2014  18  Nov 30, 2013        @  Washington       0   
19     ATL  2014  19   Dec 2, 2013       @  San Antonio       0   
20     ATL  2014  20   Dec 4, 2013      vs  LA Clippers       1   
21     ATL  2014  21   Dec 6, 2013        vs  Cleveland       1   
22     ATL  2014  22  Dec 10, 2013    vs  Oklahoma City       0   
23     ATL  2014  23  Dec 13, 2013       vs  Washington       1   
24     ATL  2014  24  Dec 14, 2013          @  New York       0   
25     ATL  2014  25  Dec 16, 2013        vs  LA Lakers       1   
26     ATL  2014  26  Dec 18, 2013       vs  Sacramento       1   
27     ATL  2014  27  Dec 20, 2013             vs  Utah       1   
28     ATL  2014  28  Dec 23, 2013             @  Miami       0   
29     ATL  2014  29  Dec 26, 2013         @  Cleveland       1   
30     ATL  2014  30  Dec 28, 2013        vs  Charlotte       1   
...    ...   ...  ..           ...                  ...     ...   
12271  MIA  2018  53   Feb 3, 2018           @  Detroit       0   
12272  MIA  2018  54   Feb 5, 2018          vs  Orlando       0   
12273  MIA  2018  55   Feb 7, 2018          vs  Houston       0   
12274  MIA  2018  56   Feb 9, 2018        vs  Milwaukee       1   
12275  MIA  2018  57  Feb 13, 2018           @  Toronto       0   
12276  MIA  2018  58  Feb 14, 2018      @  Philadelphia       0   
12277  MIA  2018  59  Feb 23, 2018       @  New Orleans       0   
12278  MIA  2018  60  Feb 24, 2018          vs  Memphis       1   
12279  MIA  2018  61  Feb 27, 2018     vs  Philadelphia       1   
12280  MIA  2018  62   Mar 1, 2018        vs  LA Lakers       0   
12281  MIA  2018  63   Mar 3, 2018          vs  Detroit       1   
12282  MIA  2018  64   Mar 5, 2018          vs  Phoenix       1   
12283  MIA  2018  65   Mar 6, 2018        @  Washington       0   
12284  MIA  2018  66   Mar 8, 2018     vs  Philadelphia       1   
12285  MIA  2018  67  Mar 10, 2018       vs  Washington       1   
12286  MIA  2018  68  Mar 12, 2018          @  Portland       0   
12287  MIA  2018  69  Mar 14, 2018        @  Sacramento       0   
12288  MIA  2018  70  Mar 16, 2018         @  LA Lakers       1   
12289  MIA  2018  71  Mar 19, 2018           vs  Denver       1   
12290  MIA  2018  72  Mar 21, 2018         vs  New York       1   
12291  MIA  2018  73  Mar 23, 2018     @  Oklahoma City       0   
12292  MIA  2018  74  Mar 25, 2018           @  Indiana       0   
12293  MIA  2018  75  Mar 27, 2018        vs  Cleveland       1   
12294  MIA  2018  76  Mar 29, 2018          vs  Chicago       1   
12295  MIA  2018  77  Mar 31, 2018         vs  Brooklyn       0   
12296  MIA  2018  78   Apr 3, 2018          vs  Atlanta       1   
12297  MIA  2018  79   Apr 4, 2018           @  Atlanta       1   
12298  MIA  2018  80   Apr 6, 2018          @  New Yo

In [132]:
import pickle

In [134]:
df.to_pickle('spread_df.pkl')

In [137]:
boxscores = client.boxscores

In [138]:
teams = ['ATL','BOS','BRK','CHI','CHO','CLE','DAL','DEN','DET','GSW','HOU','IND','LAC','LAL','MEM','MIL','MIN','NOP','NYK','OKC','ORL', \
'PHI','PHO','POR','SAC','SAS','TOR','UTA','WAS','MIA']

In [139]:
len(teams)


30

In [140]:
boxscoresunified = client['boxscoresunified']

In [141]:
boxscoresunified

Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'boxscoresunified')

In [142]:
for team in teams:
    for row in boxscores[team].find():
        row['team'] = team
        boxscoresunified.unified.insert_one(row)

In [143]:
boxscores = pd.DataFrame(list(boxscoresunified.unified.find()))

In [151]:
boxscores.to_pickle('boxscoresdf.pkl',compression='zip')

In [145]:
25223/30/10/82

1.0253252032520326

In [157]:
df

team  year   g          date                  opp  result  \
1      ATL  2014   1  Oct 30, 2013            @  Dallas       0   
2      ATL  2014   2   Nov 1, 2013          vs  Toronto       1   
3      ATL  2014   3   Nov 3, 2013         @  LA Lakers       0   
4      ATL  2014   4   Nov 5, 2013        @  Sacramento       1   
5      ATL  2014   5   Nov 7, 2013            @  Denver       0   
6      ATL  2014   6   Nov 9, 2013          vs  Orlando       1   
7      ATL  2014   7  Nov 11, 2013         @  Charlotte       1   
8      ATL  2014   8  Nov 13, 2013         vs  New York       0   
9      ATL  2014   9  Nov 15, 2013     vs  Philadelphia       1   
10     ATL  2014  10  Nov 16, 2013          @  New York       1   
11     ATL  2014  11  Nov 19, 2013             @  Miami       0   
12     ATL  2014  12  Nov 20, 2013          vs  Detroit       1   
13     ATL  2014  13  Nov 22, 2013           @  Detroit       1   
14     ATL  2014  14  Nov 23, 2013           vs  Boston       0   
15     ATL  2014  15  Nov 26, 2013          vs  Orlando       0   
16     ATL  2014  16  Nov 27, 2013           @  Houston       0   
17     ATL  2014  17  Nov 29, 2013           vs  Dallas       1   
18     ATL  2014  18  Nov 30, 2013        @  Washington       0   
19     ATL  2014  19   Dec 2, 2013       @  San Antonio       0   
20     ATL  2014  20   Dec 4, 2013      vs  LA Clippers       1   
21     ATL  2014  21   Dec 6, 2013        vs  Cleveland       1   
22     ATL  2014  22  Dec 10, 2013    vs  Oklahoma City       0   
23     ATL  2014  23  Dec 13, 2013       vs  Washington       1   
24     ATL  2014  24  Dec 14, 2013          @  New York       0   
25     ATL  2014  25  Dec 16, 2013        vs  LA Lakers       1   
26     ATL  2014  26  Dec 18, 2013       vs  Sacramento       1   
27     ATL  2014  27  Dec 20, 2013             vs  Utah       1   
28     ATL  2014  28  Dec 23, 2013             @  Miami       0   
29     ATL  2014  29  Dec 26, 2013         @  Cleveland       1   
30     ATL  2014  30  Dec 28, 2013        vs  Charlotte       1   
...    ...   ...  ..           ...                  ...     ...   
12271  MIA  2018  53   Feb 3, 2018           @  Detroit       0   
12272  MIA  2018  54   Feb 5, 2018          vs  Orlando       0   
12273  MIA  2018  55   Feb 7, 2018          vs  Houston       0   
12274  MIA  2018  56   Feb 9, 2018        vs  Milwaukee       1   
12275  MIA  2018  57  Feb 13, 2018           @  Toronto       0   
12276  MIA  2018  58  Feb 14, 2018      @  Philadelphia       0   
12277  MIA  2018  59  Feb 23, 2018       @  New Orleans       0   
12278  MIA  2018  60  Feb 24, 2018          vs  Memphis       1   
12279  MIA  2018  61  Feb 27, 2018     vs  Philadelphia       1   
12280  MIA  2018  62   Mar 1, 2018        vs  LA Lakers       0   
12281  MIA  2018  63   Mar 3, 2018          vs  Detroit       1   
12282  MIA  2018  64   Mar 5, 2018          vs  Phoenix       1   
12283  MIA  2018  65   Mar 6, 2018        @  Washington       0   
12284  MIA  2018  66   Mar 8, 2018     vs  Philadelphia       1   
12285  MIA  2018  67  Mar 10, 2018       vs  Washington       1   
12286  MIA  2018  68  Mar 12, 2018          @  Portland       0   
12287  MIA  2018  69  Mar 14, 2018        @  Sacramento       0   
12288  MIA  2018  70  Mar 16, 2018         @  LA Lakers       1   
12289  MIA  2018  71  Mar 19, 2018           vs  Denver       1   
12290  MIA  2018  72  Mar 21, 2018         vs  New York       1   
12291  MIA  2018  73  Mar 23, 2018     @  Oklahoma City       0   
12292  MIA  2018  74  Mar 25, 2018           @  Indiana       0   
12293  MIA  2018  75  Mar 27, 2018        vs  Cleveland       1   
12294  MIA  2018  76  Mar 29, 2018          vs  Chicago       1   
12295  MIA  2018  77  Mar 31, 2018         vs  Brooklyn       0   
12296  MIA  2018  78   Apr 3, 2018          vs  Atlanta       1   
12297  MIA  2018  79   Apr 4, 2018           @  Atlanta       1   
12298  MIA  2018  80   Apr 6, 2018          @  New Yo

In [158]:
ats_streak = df.ats.values

In [155]:
ats_record = np.cumsum(ats_streak)/np.arange(1,83)


In [160]:
ats_records = []
for i in range(0,150):
    streak = ats_streak[i*82:(i+1)*82]
    ats_record = np.cumsum(streak)/np.arange(1,83)
    ats_records.extend(ats_record)

In [163]:
df['ats_record'] = ats_records

In [230]:
X = df[['spread','home','ats_record','total']]
y = df.ats

In [240]:
X_train, X_test, y_train, y_test = train_test_split(X,y, test_size=0.2)

In [241]:
lr = LogisticRegression()

In [242]:
lr.fit(X_train,y_train)

LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_state=None, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False)

In [243]:
lr.score(X_test,y_test)

0.5691056910569106

In [249]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import GradientBoostingClassifier

In [245]:
rc = RandomForestClassifier(n_estimators=1000)

In [246]:
rc.fit(X_train,y_train)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=1000, n_jobs=1,
            oob_score=False, random_state=None, verbose=0,
            warm_start=False)

In [247]:
rc.score(X_test,y_test)

0.532520325203252

In [250]:
gbc = GradientBoostingClassifier(n_estimators=500)

In [251]:
gbc.fit(X_train,y_train)

GradientBoostingClassifier(criterion='friedman_mse', init=None,
              learning_rate=0.1, loss='deviance', max_depth=3,
              max_features=None, max_leaf_nodes=None,
              min_impurity_decrease=0.0, min_impurity_split=None,
              min_samples_leaf=1, min_samples_split=2,
              min_weight_fraction_leaf=0.0, n_estimators=500,
              presort='auto', random_state=None, subsample=1.0, verbose=0,
              warm_start=False)

In [287]:
soup= BeautifulSoup(boxscores.content[0],'html.parser')

In [293]:
soup.select('span.section_anchor')

[<span class="section_anchor" data-label="All Games This Date" id="other_scores_link"></span>,
 <span class="section_anchor" data-label="Line Score" id="line_score_link"></span>,
 <span class="section_anchor" data-label="Four Factors" id="four_factors_link"></span>,
 <span class="section_anchor" data-label="Dallas Mavericks (1-1)" id="box_dal_basic_link"></span>,
 <span class="section_anchor" data-label="" id="box_dal_advanced_link"></span>,
 <span class="section_anchor" data-label="Atlanta Hawks (1-0)" id="box_atl_basic_link"></span>,
 <span class="section_anchor" data-label="" id="box_atl_advanced_link"></span>,
 <span class="section_anchor" data-label="Team and League Schedules" data-no-inpage="1" id="inner_nav_bottom_link"></span>,
 <span class="section_anchor" data-label="Full Site Menu" data-no-inpage="1" id="site_menu_link"></span>,
 <span class="section_anchor" data-label="We're Social...for Statheads" data-no-inpage="1" id="_link"></span>,
 <span class="section_anchor" data-la

In [329]:

def scrape_stats_from_page(html,team:str):
    soup = BeautifulSoup(html, 'html.parser')
    items = soup.select(f'#box_{team.lower()}_basic tfoot tr td')
    return {item.attrs.get('data-stat'): item.text for item in items}

In [354]:
#gets home and opponent stats
def scrape_stats_from_df(df,teams):
    lst = []
    for i in range(len(df)):
        home = df.team[i]
        html = df.content[i]
        year = df.year[i]
        soup = BeautifulSoup(html,'html.parser')
        for team in teams:
            if team == home:
                items = soup.select(f'#box_{home.lower()}_basic tfoot tr td')
                homestat = {item.attrs.get('data-stat'): item.text for item in items}
            else:
                items = soup.select(f'#box_{team.lower()}_basic tfoot tr td')
                if items:
                    opp = {item.attrs.get('data-stat'): item.text for item in items}
        lst.append((home,year,homestat, opp))
    return lst

In [355]:
boxscores

_id  \
0      5b66912cf227df0bf9c10ec9   
1      5b669130f227df0bf9c10eca   
2      5b669133f227df0bf9c10ecb   
3      5b669136f227df0bf9c10ecc   
4      5b66913af227df0bf9c10ecd   
5      5b66913df227df0bf9c10ece   
6      5b669140f227df0bf9c10ecf   
7      5b669144f227df0bf9c10ed0   
8      5b669147f227df0bf9c10ed1   
9      5b66914bf227df0bf9c10ed2   
10     5b66914ef227df0bf9c10ed3   
11     5b669152f227df0bf9c10ed4   
12     5b669155f227df0bf9c10ed5   
13     5b669158f227df0bf9c10ed6   
14     5b66915df227df0bf9c10ed7   
15     5b669160f227df0bf9c10ed8   
16     5b669164f227df0bf9c10ed9   
17     5b669167f227df0bf9c10eda   
18     5b66916af227df0bf9c10edb   
19     5b66916ef227df0bf9c10edc   
20     5b669171f227df0bf9c10edd   
21     5b669174f227df0bf9c10ede   
22     5b669178f227df0bf9c10edf   
23     5b66917bf227df0bf9c10ee0   
24     5b66917ef227df0bf9c10ee1   
25     5b669182f227df0bf9c10ee2   
26     5b669185f227df0bf9c10ee3   
27     5b669189f227df0bf9c10ee4   
28     5b66918cf227df0bf9c10ee5   
29     5b66918ff227df0bf9c10ee6   
...                         ...   
25193  5b67e1c7f227df0bf9c17132   
25194  5b67e1caf227df0bf9c17133   
25195  5b67e1cdf227df0bf9c17134   
25196  5b67e1d1f227df0bf9c17135   
25197  5b67e1d4f227df0bf9c17136   
25198  5b67e1d8f227df0bf9c17137   
25199  5b67e1dbf227df0bf9c17138   
25200  5b67e1def227df0bf9c17139   
25201  5b67e1e2f227df0bf9c1713a   
25202  5b67e1e5f227df0bf9c1713b   
25203  5b67e1e9f227df0bf9c1713c   
25204  5b67e1ecf227df0bf9c1713d   
25205  5b67e1eff227df0bf9c1713e   
25206  5b67e1f3f227df0bf9c1713f   
25207  5b67e1f6f227df0bf9c17140   
25208  5b67e1faf227df0bf9c17141   
25209  5b67e1fdf227df0bf9c17142   
25210  5b67e200f227df0bf9c17143   
25211  5b67e204f227df0bf9c17144   
25212  5b67e207f227df0bf9c17145   
25213  5b67e20bf227df0bf9c17146   
25214  5b67e20ef227df0bf9c17147   
25215  5b67e211f227df0bf9c17148   
25216  5b67e215f227df0bf9c17149   
25217  5b67e218f227df0bf9c1714a   
25218  5b67e21cf227df0bf9c1714b   
25219  5b67e21ff227df0bf9c1714c   
25220  5b67e223f227df0bf9c1714d   
25221  5b67e226f227df0bf9c1714e   
25222  5b67e229f227df0bf9c1714f   

                                                 content team  \
0      b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
1      b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
2      b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
3      b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
4      b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
5      b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
6      b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
7      b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
8      b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
9      b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
10     b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
11     b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
12     b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
13     b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
14     b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
15     b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
16     b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
17     b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
18     b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
19     b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
20     b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
21     b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
22     b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
23     b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
24     b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
25     b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
26     b'\n<!DOCTYPE html>\n<html data-version="kleck...  ATL   
27     b'\n<!DOCTYPE html>\n<html dat

In [356]:
test_df = copy.deepcopy(boxscores[:5])

In [357]:
clean_test_data = scrape_stats_from_df(test_df,teams)

In [358]:
clean_test_data

[('ATL',
  '2008',
  {'mp': '240',
   'fg': '36',
   'fga': '79',
   'fg_pct': '.456',
   'fg3': '4',
   'fg3a': '15',
   'fg3_pct': '.267',
   'ft': '25',
   'fta': '31',
   'ft_pct': '.806',
   'orb': '14',
   'drb': '38',
   'trb': '52',
   'ast': '20',
   'stl': '6',
   'blk': '4',
   'tov': '15',
   'pf': '23',
   'pts': '101',
   'plus_minus': ''},
  {'mp': '240',
   'fg': '35',
   'fga': '80',
   'fg_pct': '.438',
   'fg3': '4',
   'fg3a': '24',
   'fg3_pct': '.167',
   'ft': '20',
   'fta': '25',
   'ft_pct': '.800',
   'orb': '7',
   'drb': '31',
   'trb': '38',
   'ast': '14',
   'stl': '4',
   'blk': '10',
   'tov': '10',
   'pf': '25',
   'pts': '94',
   'plus_minus': ''}),
 ('ATL',
  '2008',
  {'mp': '240',
   'fg': '33',
   'fga': '72',
   'fg_pct': '.458',
   'fg3': '4',
   'fg3a': '10',
   'fg3_pct': '.400',
   'ft': '21',
   'fta': '26',
   'ft_pct': '.808',
   'orb': '12',
   'drb': '29',
   'trb': '41',
   'ast': '15',
   'stl': '8',
   'blk': '7',
   'tov': '19',
  

In [359]:
clean_test_df = pd.DataFrame(data=clean_test_data)

In [1]:
[boxscores.team =='CHO']

NameError: name 'boxscores' is not defined

In [362]:
scrape_stats_from_df(boxscores,teams)

[('ATL',
  '2008',
  {'mp': '240',
   'fg': '36',
   'fga': '79',
   'fg_pct': '.456',
   'fg3': '4',
   'fg3a': '15',
   'fg3_pct': '.267',
   'ft': '25',
   'fta': '31',
   'ft_pct': '.806',
   'orb': '14',
   'drb': '38',
   'trb': '52',
   'ast': '20',
   'stl': '6',
   'blk': '4',
   'tov': '15',
   'pf': '23',
   'pts': '101',
   'plus_minus': ''},
  {'mp': '240',
   'fg': '35',
   'fga': '80',
   'fg_pct': '.438',
   'fg3': '4',
   'fg3a': '24',
   'fg3_pct': '.167',
   'ft': '20',
   'fta': '25',
   'ft_pct': '.800',
   'orb': '7',
   'drb': '31',
   'trb': '38',
   'ast': '14',
   'stl': '4',
   'blk': '10',
   'tov': '10',
   'pf': '25',
   'pts': '94',
   'plus_minus': ''}),
 ('ATL',
  '2008',
  {'mp': '240',
   'fg': '33',
   'fga': '72',
   'fg_pct': '.458',
   'fg3': '4',
   'fg3a': '10',
   'fg3_pct': '.400',
   'ft': '21',
   'fta': '26',
   'ft_pct': '.808',
   'orb': '12',
   'drb': '29',
   'trb': '41',
   'ast': '15',
   'stl': '8',
   'blk': '7',
   'tov': '19',
  

In [363]:
longlist = _
#data = [[v for k,v in item.items()] for item in houbox]

In [364]:
large_box_df = pd.DataFrame(data=longlist)

In [3]:
large_box_df[1]

NameError: name 'large_box_df' is not defined

In [450]:
h = large_box_df[2].apply(pd.Series)
h.drop(columns='plus_minus',inplace=True)
h_trans = h.applymap(lambda x:float(x))
h_trans

mp    fg    fga  fg_pct   fg3  fg3a  fg3_pct    ft   fta  ft_pct  \
0      240.0  36.0   79.0   0.456   4.0  15.0    0.267  25.0  31.0   0.806   
1      240.0  33.0   72.0   0.458   4.0  10.0    0.400  21.0  26.0   0.808   
2      240.0  26.0   68.0   0.382   7.0  18.0    0.389  23.0  32.0   0.719   
3      240.0  41.0   90.0   0.456   4.0  16.0    0.250  19.0  23.0   0.826   
4      240.0  30.0   70.0   0.429   5.0  11.0    0.455  18.0  25.0   0.720   
5      240.0  30.0   77.0   0.390   3.0  20.0    0.150  27.0  35.0   0.771   
6      240.0  46.0   77.0   0.597   3.0   6.0    0.500  22.0  27.0   0.815   
7      290.0  45.0   99.0   0.455   6.0  23.0    0.261  27.0  33.0   0.818   
8      240.0  40.0   84.0   0.476   2.0  13.0    0.154  14.0  23.0   0.609   
9      240.0  33.0   79.0   0.418   0.0   8.0    0.000  17.0  24.0   0.708   
10     240.0  27.0   77.0   0.351   6.0  16.0    0.375  22.0  28.0   0.786   
11     240.0  36.0   80.0   0.450   6.0  13.0    0.462  16.0  20.0   0.800   
12     240.0  27.0   68.0   0.397   4.0  11.0    0.364  20.0  30.0   0.667   
13     240.0  35.0   74.0   0.473   6.0  11.0    0.545  20.0  24.0   0.833   
14     240.0  31.0   68.0   0.456   6.0  15.0    0.400  18.0  25.0   0.720   
15     240.0  37.0   83.0   0.446   3.0  17.0    0.176  11.0  15.0   0.733   
16     240.0  32.0   74.0   0.432   4.0  12.0    0.333  27.0  30.0   0.900   
17     240.0  30.0   74.0   0.405   1.0  11.0    0.091  29.0  37.0   0.784   
18     240.0  34.0   84.0   0.405   4.0  13.0    0.308  14.0  19.0   0.737   
19     240.0  35.0   82.0   0.427   5.0  11.0    0.455  23.0  30.0   0.767   
20     240.0  31.0   80.0   0.388   5.0  10.0    0.500  21.0  26.0   0.808   
21     240.0  27.0   76.0   0.355   0.0   5.0    0.000  27.0  35.0   0.771   
22     240.0  33.0   68.0   0.485   5.0  12.0    0.417  22.0  30.0   0.733   
23     240.0  38.0   66.0   0.576   4.0  12.0    0.333  36.0  50.0   0.720   
24     265.0  41.0   79.0   0.519   1.0  11.0    0.091  31.0  36.0   0.861   
25     240.0  33.0   73.0   0.452   7.0  12.0    0.583  24.0  30.0   0.800   
26     240.0  38.0   84.0   0.452   5.0   8.0    0.625  26.0  30.0   0.867   
27     240.0  30.0   72.0   0.417   1.0   6.0    0.167  23.0  31.0   0.742   
28     240.0  31.0   76.0   0.408   5.0  11.0    0.455  27.0  34.0   0.794   
29     240.0  32.0   75.0   0.427   1.0  10.0    0.100  26.0  32.0   0.813   
...      ...   ...    ...     ...   ...   ...      ...   ...   ...     ...   
25193  240.0  34.0   87.0   0.391  12.0  37.0    0.324  17.0  26.0   0.654   
25194  240.0  44.0   91.0   0.484  14.0  36.0    0.389   5.0   7.0   0.714   
25195  240.0  40.0   93.0   0.430   3.0  23.0    0.130  26.0  35.0   0.743   
25196  240.0  39.0   88.0   0.443  13.0  32.0    0.406  10.0  12.0   0.833   
25197  240.0  32.0   88.0   0.364  10.0  26.0    0.385  17.0  18.0   0.944   
25198  240.0  42.0   86.0   0.488  12.0  29.0    0.414  16.0  19.0   0.842   
25199  240.0  35.0   77.0   0.455  11.0  27.0    0.407  21.0  29.0   0.724   
25200  265.0  50.0  108.0   0.463   6.0  18.0    0.333  17.0  26.0   0.654   
25201  240.0  41.0   89.0   0.461  12.0  33.0    0.364  21.0  27.0   0.778   
25202  240.0  36.0   82.0   0.439   9.0  27.0    0.333  21.0  28.0   0.750   
25203  240.0  46.0   95.0   0.484   9.0  31.0    0.290  12.0  16.0   0.750   
25204  240.0  37.0   82.0   0.451  12.0  29.0    0.414  19.0  28.0   0.679   
25205  240.0  47.0   92.0   0.511  12.0  36.0    0.333  19.0  23.0   0.826   
25206  265.0  42.0   94.0   0.447   9.0  33.0    0.273  20.0  27.0   0.741   
25207  240.0  42.0   89.0   0.472  14.0  26.0    0.538  10.0  18.0   0.556   
25208  240.0  52.0   88.0   0.591  10.0  28.0    0.357  15.0  21.0   0.714   
25209  240.0  39.0   91.0   0.429  10.0  31.0    0.323  11.0  16.0   0.688   
25210  265.0  41.0   99.0   0.414  18.0  43.0    0.419  19.0  21.0   0.905   
25211  240.0  36.0   94.0   0.383  10.0  36.0    0.278  10.0  14.0   0.714   
25212  290.0  56.0  102.0   0.54

In [451]:
#find more efficient way to code my function
o = large_box_df[3].apply(pd.Series)
o.drop(columns='plus_minus',inplace=True)
o_trans = o.applymap(lambda x:float(x))
o_trans

mp    fg    fga  fg_pct   fg3  fg3a  fg3_pct    ft   fta  ft_pct  \
0      240.0  35.0   80.0   0.438   4.0  24.0    0.167  20.0  25.0   0.800   
1      240.0  37.0   81.0   0.457   4.0  14.0    0.286  14.0  21.0   0.667   
2      240.0  37.0   81.0   0.457   4.0  14.0    0.286  14.0  21.0   0.667   
3      240.0  35.0   86.0   0.407  11.0  27.0    0.407  15.0  17.0   0.882   
4      240.0  41.0   68.0   0.603   6.0  10.0    0.600  18.0  25.0   0.720   
5      240.0  38.0   88.0   0.432   5.0  17.0    0.294  20.0  25.0   0.800   
6      240.0  38.0   88.0   0.432   5.0  17.0    0.294  20.0  25.0   0.800   
7      240.0  38.0   88.0   0.432   5.0  17.0    0.294  20.0  25.0   0.800   
8      240.0  45.0   86.0   0.523   5.0  12.0    0.417  10.0  16.0   0.625   
9      240.0  38.0   76.0   0.500   7.0  17.0    0.412  12.0  15.0   0.800   
10     240.0  25.0   59.0   0.424   3.0   9.0    0.333  26.0  35.0   0.743   
11     240.0  34.0   72.0   0.472   3.0  13.0    0.231  16.0  21.0   0.762   
12     240.0  35.0   88.0   0.398   5.0  12.0    0.417  15.0  22.0   0.682   
13     240.0  31.0   70.0   0.443   3.0  17.0    0.176  15.0  19.0   0.789   
14     240.0  31.0   70.0   0.443   3.0  17.0    0.176  15.0  19.0   0.789   
15     240.0  30.0   75.0   0.400   2.0  11.0    0.182  17.0  25.0   0.680   
16     240.0  42.0   81.0   0.519   6.0  10.0    0.600  16.0  17.0   0.941   
17     240.0  37.0   95.0   0.389   4.0  10.0    0.400  11.0  14.0   0.786   
18     240.0  32.0   78.0   0.410   1.0  15.0    0.067  13.0  16.0   0.813   
19     240.0  29.0   73.0   0.397  11.0  31.0    0.355  18.0  30.0   0.600   
20     240.0  36.0   80.0   0.450   5.0  11.0    0.455  23.0  29.0   0.793   
21     240.0  33.0   73.0   0.452   4.0  15.0    0.267  21.0  29.0   0.724   
22     240.0  33.0   73.0   0.452   4.0  15.0    0.267  21.0  29.0   0.724   
23     240.0  40.0   83.0   0.482   2.0   8.0    0.250  29.0  42.0   0.690   
24     265.0  33.0   71.0   0.465   3.0   9.0    0.333  42.0  49.0   0.857   
25     240.0  33.0   74.0   0.446   9.0  24.0    0.375  17.0  22.0   0.773   
26     240.0  35.0   84.0   0.417   8.0  25.0    0.320  17.0  23.0   0.739   
27     240.0  32.0   73.0   0.438   7.0  13.0    0.538  26.0  35.0   0.743   
28     240.0  39.0   77.0   0.506   3.0  11.0    0.273  17.0  23.0   0.739   
29     240.0  41.0   86.0   0.477  13.0  25.0    0.520  18.0  28.0   0.643   
...      ...   ...    ...     ...   ...   ...      ...   ...   ...     ...   
25193  240.0  42.0   85.0   0.494   8.0  24.0    0.333  11.0  15.0   0.733   
25194  240.0  44.0   84.0   0.524   9.0  26.0    0.346  14.0  17.0   0.824   
25195  240.0  41.0   84.0   0.488  13.0  30.0    0.433  16.0  19.0   0.842   
25196  240.0  38.0   74.0   0.514  12.0  31.0    0.387  21.0  26.0   0.808   
25197  240.0  32.0   76.0   0.421   6.0  20.0    0.300  15.0  17.0   0.882   
25198  240.0  42.0   90.0   0.467  13.0  35.0    0.371  18.0  23.0   0.783   
25199  240.0  39.0   92.0   0.424   9.0  35.0    0.257  17.0  25.0   0.680   
25200  265.0  48.0  108.0   0.444   8.0  31.0    0.258  20.0  24.0   0.833   
25201  240.0  35.0   80.0   0.438   5.0  11.0    0.455  14.0  17.0   0.824   
25202  240.0  35.0   84.0   0.417  12.0  31.0    0.387  19.0  23.0   0.826   
25203  240.0  47.0   79.0   0.595  16.0  29.0    0.552  21.0  26.0   0.808   
25204  240.0  37.0   89.0   0.416   7.0  24.0    0.292  15.0  21.0   0.714   
25205  240.0  42.0   87.0   0.483  10.0  24.0    0.417   9.0  18.0   0.500   
25206  265.0  40.0   80.0   0.500  14.0  24.0    0.583  23.0  27.0   0.852   
25207  240.0  34.0   86.0   0.395  15.0  37.0    0.405  16.0  21.0   0.762   
25208  240.0  34.0   77.0   0.442   7.0  20.0    0.350  27.0  34.0   0.794   
25209  240.0  38.0   83.0   0.458  14.0  36.0    0.389  25.0  30.0   0.833   
25210  265.0  48.0   94.0   0.511   8.0  24.0    0.333  19.0  25.0   0.760   
25211  240.0  32.0   76.0   0.421   9.0  19.0    0.474  18.0  22.0   0.818   
25212  290.0  46.0  100.0   0.46

In [452]:
opponents = o_trans.columns

In [454]:
o_idx = ['opp_' + x for x in opponents]

In [455]:
o_trans.columns = o_idx

In [456]:
final_df = pd.concat([large_box_df,h_trans,o_trans],axis=1,copy=True)

In [457]:
final_df.drop(columns=[2,3],inplace=True)

In [406]:
#final_df.drop(columns=['plus_minus','opp_plus_minus'],inplace=True)

In [458]:
final_df.to_pickle('final_df.pkl')

In [459]:
data = pd.read_pickle('final_df.pkl')

In [460]:
indexes = data.columns.values 

In [461]:
indexes[0] = 'team'

In [462]:
indexes[1] = 'year'

In [463]:
data.columns = indexes

In [464]:
data.year[9]

'2008'

In [465]:
houston_2017 = copy.deepcopy(data[(data['team'] == 'HOU') & (data['year']=='2017')])

In [466]:
houston_2017.index = range(1,83)

In [538]:
hou_avg_2017 = (houston_2017.mean(), houston_2017.std())

In [477]:
hou_spread_2017 = copy.deepcopy(df[(df['team'] == 'HOU') & (df['year']=='2017')])

In [479]:
hou_spread_2017.index = range(1,83)

In [481]:
hou_comb = pd.concat([houston_2017,hou_spread_2017], axis=1,copy=True)

In [500]:
y = hou_comb.ats.values
hou_comb_clean = hou_comb.drop(columns=['team','year','score','ou','date','opp','ats_record','ats'])

In [501]:
X = hou_comb_clean

In [507]:
X_train, X_test, y_train, y_test = train_test_split(X,y,test_size = .33)

In [508]:
lr.fit(X_train,y_train)

LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_state=None, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False)

In [509]:
lr.score(X_test,y_test)

0.9285714285714286

In [512]:
lr.coef_

array([[ 1.94669257e-02,  7.78994344e-02, -7.79793317e-02,
         1.79343501e-03,  4.10057304e-02, -1.72257623e-01,
         2.35833400e-03, -1.50718854e-01, -1.23816805e-01,
        -2.62164089e-03,  1.63120351e-02, -4.24248282e-02,
        -2.61127931e-02,  1.03406918e-01, -1.58231255e-01,
        -3.22785052e-02, -7.29457747e-02, -6.40084435e-02,
         4.60857449e-02,  1.94669257e-02, -7.54644527e-02,
         7.22495724e-02, -7.39206776e-04,  1.89823948e-02,
        -1.25228086e-01,  2.15817857e-03, -2.36615669e-02,
         8.87400399e-03,  3.42081307e-04,  1.43411348e-01,
        -2.29137033e-01, -8.57256850e-02, -5.00208802e-02,
        -7.37646553e-02,  4.29912854e-02, -2.26210174e-01,
        -7.94418187e-02, -1.55608077e-01, -6.05789830e-02,
        -1.76116671e-02,  3.63199381e-01,  1.90341604e-01,
        -1.85076416e-02,  2.01693822e-01,  5.64893203e-01]])

In [562]:
hou_avg_2017[1]

mp              6.692587
fg              4.697488
fga             6.592222
fg_pct          0.052653
fg3             4.112191
fg3a            7.077835
fg3_pct         0.082657
ft              6.170529
fta             7.398953
ft_pct          0.084323
orb             3.739645
drb             5.969560
trb             7.268250
ast             4.665505
stl             3.078419
blk             2.140081
tov             4.080196
pf              3.832224
pts            12.102667
opp_mp          6.692587
opp_fg          4.333246
opp_fga         7.545945
opp_fg_pct      0.052905
opp_fg3         2.968975
opp_fg3a        6.093433
opp_fg3_pct     0.083062
opp_ft          5.225321
opp_fta         6.194637
opp_ft_pct      0.090078
opp_orb         4.223648
opp_drb         5.102340
opp_trb         6.500423
opp_ast         4.783620
opp_stl         3.019484
opp_blk         2.457008
opp_tov         4.503420
opp_pf          3.937635
opp_pts        11.040923
dtype: float64

In [546]:
import scipy.stats as stats

In [566]:
k = tuple(zip(hou_avg_2017[0],hou_avg_2017[1]))

In [567]:
k

((241.21951219512195, 6.692587368502161),
 (40.30487804878049, 4.697488229251526),
 (87.21951219512195, 6.592222110313129),
 (0.4632804878048781, 0.052653367845163716),
 (14.402439024390244, 4.112191317838663),
 (40.31707317073171, 7.077835424116347),
 (0.3561829268292683, 0.08265727665439083),
 (20.329268292682926, 6.170529076799185),
 (26.548780487804876, 7.398952943982608),
 (0.7647560975609757, 0.08432338705445862),
 (10.878048780487806, 3.739644942222106),
 (33.48780487804878, 5.969560445466203),
 (44.36585365853659, 7.268250243899796),
 (25.24390243902439, 4.665505081915214),
 (8.170731707317072, 3.0784190188350653),
 (4.2926829268292686, 2.1400807927407772),
 (14.487804878048781, 4.0801957785242395),
 (19.926829268292682, 3.832223632630383),
 (115.34146341463415, 12.102667303395133),
 (241.21951219512195, 6.692587368502161),
 (41.15853658536585, 4.333246472619825),
 (88.85365853658537, 7.545944788173368),
 (0.465268292682927, 0.052904537549678846),
 (10.0, 2.9689753813083084),
 